In [1]:
import glob
import gc
from datetime import datetime, timedelta
import numpy as np 
import pandas as pd
import geopandas as gpd
import plotly.express as px
import plotly.graph_objs as go
import plotly.express as px
import plotly.graph_objs as go
from utils_covid import fix_country_names, get_names

In [77]:
def get_large_to_long_format_JHU_data(df, col_values='Confirmed'):
    dates = df.columns[4:]
    df = df.melt(id_vars=['Province/State',
                          'Country/Region', 
                          'Lat', 
                          'Long'],
                 value_vars=dates, 
                 var_name='Date', 
                 value_name=col_values)
    return df

In [3]:
def merge_JHU_data_frames(df1, df2, df3):
    full_df = pd.merge(left=df1, right=df2, how='left',
                      on=['Province/State', 'Country/Region', 'Date', 'Lat', 'Long'])
    full_df = pd.merge(left=full_df, right=df3, how='left',
                      on=['Province/State', 'Country/Region', 'Date', 'Lat', 'Long'])
    return full_df

In [1]:
def fix_country_names(tmp_df):
    '''
    Cleaning up after JHU's bullshit data management
    '''
    # Asian Countries
    tmp_df['country'] = np.where((tmp_df['country']  == 'Mainland China'),'China', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Korea, South'),'South Korea', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Republic of Korea'),'South Korea', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Hong Kong SAR'),'Hong Kong', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Taipei and environs'),'Taiwan', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Taiwan*'),'Taiwan', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Macao SAR'),'Macau', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Iran (Islamic Republic of)'),'Iran', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Viet Nam'),'Vietnam', tmp_df['country'])

    #European Countries
    tmp_df['country'] = np.where((tmp_df['country']  == 'UK'),'United Kingdom', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == ' Azerbaijan'),'Azerbaijan', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Bosnia and Herzegovina'),'Bosnia', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Czech Republic'),'Czechia', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Republic of Ireland'),'Ireland', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'North Ireland'),'Ireland', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Republic of Moldova'),'Moldova', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Russian Federation'),'Russia', tmp_df['country'])

    #African Countries
    tmp_df['country'] = np.where((tmp_df['country']  == 'Congo (Brazzaville)'),'Congo', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Congo (Kinshasa)'),'Congo', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Republic of the Congo'),'Congo', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Gambia, The'),'Gambia', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'The Gambia'),'Gambia', tmp_df['country'])

    # Western Countries
    tmp_df['country'] = np.where((tmp_df['country']  == 'USA'),'America', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'US'),'America', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Bahamas, The'),'The Bahamas', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'Bahamas'),'The Bahamas', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'st. Martin'),'Saint Martin', tmp_df['country'])
    tmp_df['country'] = np.where((tmp_df['country']  == 'St. Martin'),'Saint Martin', tmp_df['country'])
    

    # Others
    tmp_df['country'] = np.where((tmp_df['country']  == 'Cruise Ship'),'Others', tmp_df['country'])

    return tmp_df

In [79]:
gc.collect()

5352

In [5]:
today = datetime.utcnow().date()
yesterday = today - timedelta(days=1)
ontem = yesterday.strftime('%d/%m/%y')

#### Loading data in

In [6]:
path = '/home/paulo/Documents/Projetos/UFSC_Covid/Data/New'

In [7]:
# reading all the csvs
all_files = glob.glob(path + "/*.csv")

for filename in all_files:
    print(filename)

/home/paulo/Documents/Projetos/UFSC_Covid/Data/New/world_covid_daily_2021-04-14.csv
/home/paulo/Documents/Projetos/UFSC_Covid/Data/New/country_week_latest_2021-04-14.csv
/home/paulo/Documents/Projetos/UFSC_Covid/Data/New/world_covid_clean_2021-04-14.csv
/home/paulo/Documents/Projetos/UFSC_Covid/Data/New/world_covid_grouped_2021-04-14.csv


In [19]:
iso = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))
iso[['name', 'iso_a3']]

name iso_a3
0                        Fiji    FJI
1                    Tanzania    TZA
2                   W. Sahara    ESH
3                      Canada    CAN
4    United States of America    USA
..                        ...    ...
172                    Serbia    SRB
173                Montenegro    MNE
174                    Kosovo    -99
175       Trinidad and Tobago    TTO
176                  S. Sudan    SSD

[177 rows x 2 columns]

In [20]:
iso.head()

pop_est      continent                      name iso_a3  gdp_md_est  \
0     920938        Oceania                      Fiji    FJI      8374.0   
1   53950935         Africa                  Tanzania    TZA    150600.0   
2     603253         Africa                 W. Sahara    ESH       906.5   
3   35623680  North America                    Canada    CAN   1674000.0   
4  326625791  North America  United States of America    USA  18560000.0   

                                            geometry  
0  MULTIPOLYGON (((180.00000 -16.06713, 180.00000...  
1  POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...  
2  POLYGON ((-8.66559 27.65643, -8.66512 27.58948...  
3  MULTIPOLYGON (((-122.84000 49.00000, -122.9742...  
4  MULTIPOLYGON (((-122.84000 49.00000, -120.0000...

In [ ]:
# dif = [name for name in nomes if name not in set(world_cov_grouped['country'].values)]

In [21]:
iso.shape

(177, 6)

In [ ]:
# world_small = world_small[~world_small['country'].isin(drop)]

In [ ]:
# iso = world_small.copy()
# for ol, nw in zip(old, new):
#     mask = iso['country'].str.startswith(ol)
#     iso.loc[mask, 'country'] = nw

In [ ]:
# # the alterations
# assert iso[iso['country'] == 'Brunei Darussalam'].empty == True
# assert iso[iso['country'] == "Côte d'Ivoire"].empty == True
# assert iso[iso['country'] == 'Russian Federation'].empty == True
# assert iso[iso['country'] == 'Venezuela (Bolivarian Republic of)'].empty == True
# assert iso[iso['country'] == 'Tanzania, United Republic of'].empty == True

In [ ]:
# del old
# del new
# del drop
# del world_small

In [ ]:
# world_covid_grouped, world_covid_clean, world_covid_daily, country_week_latest = dfs

In [ ]:
(world_covid_grouped[['confirmed', 'deaths', 'recovered', 'active',
       'new_confirmed', 'new_deaths', 'new_recovered']].values < 0).any()

In [ ]:
(world_covid_clean[['confirmed', 'deaths',
       'recovered', 'active']].values < 0).any()

In [ ]:
(world_covid_daily[['confirmed', 'deaths', 'recovered', 'active', 'new_confirmed',
       'new_deaths', 'new_recovered', 'deaths_100Cases', 'recovered_100Cases',
       'deaths_100recovered']].values < 0).any()

In [ ]:
(country_week_latest[['confirmed', 'deaths', 'recovered', 'active',
       'new_confirmed', 'new_deaths', 'new_recovered', 'deaths_100_cases',
       'recovered_100_cases', 'deaths_100_recovered', 'today_cases',
       'last_week_cases', 'week_dif_change', 'week_%_increase']].values < 0).any()

In [ ]:
# world_cov_grouped = pd.read_csv('Data/New/world_covid_grouped_2021-04-14.csv')

In [12]:
world_covid = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv')

In [13]:
world_covid

Province/State      Country/Region        Lat        Long  1/22/20  \
0              NaN         Afghanistan  33.939110   67.709953        0   
1              NaN             Albania  41.153300   20.168300        0   
2              NaN             Algeria  28.033900    1.659600        0   
3              NaN             Andorra  42.506300    1.521800        0   
4              NaN              Angola -11.202700   17.873900        0   
..             ...                 ...        ...         ...      ...   
269            NaN             Vietnam  14.058324  108.277199        0   
270            NaN  West Bank and Gaza  31.952200   35.233200        0   
271            NaN               Yemen  15.552727   48.516388        0   
272            NaN              Zambia -13.133897   27.849332        0   
273            NaN            Zimbabwe -19.015438   29.154857        0   

     1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  ...  4/5/21  4/6/21  4/7/21  \
0          0        0        0        0        0  ...   56717   56779   56873   
1          0        0        0        0        0  ...  126795  126936  127192   
2          0        0        0        0        0  ...  117739  117879  118004   
3          0        0        0        0        0  ...   12286   12328   12363   
4          0        0        0        0        0  ...   22717   22885   23010   
..       ...      ...      ...      ...      ...  ...     ...     ...     ...   
269        2        2        2        2        2  ...    2637    2648    2659   
270        0        0        0        0        0  ...  253922  256461  259133   
271        0        0        0        0        0  ...    4881    4975    5047   
272        0        0        0        0        0  ...   89009   89071   89386   
273        0        0        0        0        0  ...   36934   36966   36984   

     4/8/21  4/9/21  4/10/21  4/11/21  4/12/21  4/13/21  4/14/21  
0     56943   57019    57144    57160    57242    57364    57492  
1    127509  127795   128155   128393   128518   128752   128959  
2    118116  118251   118378   118516   118645   118799   118975  
3     12409   12456    12497    12545    12581    12614    12641  
4     23108   23242    23331    23457    23549    23697    23841  
..      ...     ...      ...      ...      ...      ...      ...  
269    2668    2683     2692     2693     2705     2714     2733  
270  262017  264395   265897   268132   270856   272767   274690  
271    5133    5233     5276     5357     5446     5507     5582  
272   89592   89783    89918    90029    90064    90218    90389  
273   37052   37147    37273    37288    37307    37330    37369  

[274 rows x 453 columns]

In [14]:
world_covid['Country/Region'] = world_covid['Country/Region'].replace('US', 'United States of America')

In [22]:
# reset the index to name # if not do that the df is messed up up NaN
iso.index = iso['name']

In [23]:
# Faz o reindex with the country names from the covid data frame
iso = iso.reindex(world_covid['Country/Region'])
iso

pop_est continent         name iso_a3  gdp_md_est  \
Country/Region                                                             
Afghanistan         34124811.0      Asia  Afghanistan    AFG     64080.0   
Albania              3047987.0    Europe      Albania    ALB     33900.0   
Algeria             40969443.0    Africa      Algeria    DZA    609400.0   
Andorra                    NaN       NaN          NaN    NaN         NaN   
Angola              29310273.0    Africa       Angola    AGO    189000.0   
...                        ...       ...          ...    ...         ...   
Vietnam             96160163.0      Asia      Vietnam    VNM    594900.0   
West Bank and Gaza         NaN       NaN          NaN    NaN         NaN   
Yemen               28036829.0      Asia        Yemen    YEM     73450.0   
Zambia              15972000.0    Africa       Zambia    ZMB     65170.0   
Zimbabwe            13805084.0    Africa     Zimbabwe    ZWE     28330.0   

                                                             geometry  
Country/Region                                                         
Afghanistan         POLYGON ((66.51861 37.36278, 67.07578 37.35614...  
Albania             POLYGON ((21.02004 40.84273, 20.99999 40.58000...  
Algeria             POLYGON ((-8.68440 27.39574, -8.66512 27.58948...  
Andorra                                                          None  
Angola              MULTIPOLYGON (((12.99552 -4.78110, 12.63161 -4...  
...                                                               ...  
Vietnam             POLYGON ((104.33433 10.48654, 105.19991 10.889...  
West Bank and Gaza                                               None  
Yemen               POLYGON ((52.00001 19.00000, 52.78218 17.34974...  
Zambia              POLYGON ((30.74001 -8.34001, 31.15775 -8.59458...  
Zimbabwe            POLYGON ((31.19141 -22.25151, 30.65987 -22.151...  

[274 rows x 6 columns]

In [24]:
iso['iso_a3'] = iso['iso_a3'].fillna('NaN')

In [25]:
# transfer the iso symbols to the covid data frame
world_covid['iso_a3'] = iso['iso_a3'].reset_index(drop=True)
world_covid[['iso_a3']]

iso_a3
0      AFG
1      ALB
2      DZA
3      NaN
4      AGO
..     ...
269    VNM
270    NaN
271    YEM
272    ZMB
273    ZWE

[274 rows x 1 columns]

In [42]:
date_cols = list(world_covid.columns[4:-1])

In [43]:
countries = np.array([[i] * len(date_cols) for i in world_covid['iso_a3']]).flatten()
pd.Series(date_cols)

0      1/22/20
1      1/23/20
2      1/24/20
3      1/25/20
4      1/26/20
        ...   
444    4/10/21
445    4/11/21
446    4/12/21
447    4/13/21
448    4/14/21
Length: 449, dtype: object

In [44]:
pd.Series(countries)

0         AFG
1         AFG
2         AFG
3         AFG
4         AFG
         ... 
123021    ZWE
123022    ZWE
123023    ZWE
123024    ZWE
123025    ZWE
Length: 123026, dtype: object

In [45]:
len(world_covid['Country/Region']), type(date_cols)

(274, list)

In [48]:
dates = date_cols * len(world_covid['Country/Region'])

In [52]:
gc.collect()

2688

In [55]:
def world_map(suffix):
    # downloading the world data from https://github.com/CSSEGISandData
    path = f'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_{suffix}_global.csv'
    df = pd.read_csv(path)
    df['Country/Region'] = df['Country/Region'].replace('US', 'United States of America')
    
    # getting the iso symbols for the countries
    iso = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))
    iso.index = iso['name']
    # indexing the iso df with the country column of the covid data
    iso = iso.reindex(df['Country/Region'])
    iso['iso_a3'] = iso['iso_a3'].fillna('NaN')
    # creating the iso column iith the iso a3 symbols in the covid data frame
    df['iso_a3'] = iso['iso_a3'].reset_index(drop=True)
    
    date_cols = list(df.columns[4:-1])
    countries = np.array([[i] * len(date_cols) for i in df['iso_a3']]).flatten()
    dates = date_cols * len(df['Country/Region'])
    values = np.array([list(i) for i in df[date_cols].iloc]).flatten()
    data = pd.DataFrame({'country':countries, 'date':dates, suffix:values})

    fig = px.choropleth(data, locations='country', color=suffix, animation_frame='date')
    fig.show()

In [58]:
world_map('recovered')

In [53]:
values = np.array([list(i) for i in world_covid[date_cols].iloc]).flatten()
data = pd.DataFrame({'country':countries, 'date':dates, 'confirmed':values})
data

country     date  confirmed
0          AFG  1/22/20          0
1          AFG  1/23/20          0
2          AFG  1/24/20          0
3          AFG  1/25/20          0
4          AFG  1/26/20          0
...        ...      ...        ...
123021     ZWE  4/10/21      37273
123022     ZWE  4/11/21      37288
123023     ZWE  4/12/21      37307
123024     ZWE  4/13/21      37330
123025     ZWE  4/14/21      37369

[123026 rows x 3 columns]

In [61]:
def linear(suffix, country_list):
    path = f'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_{suffix}_global.csv'
    df = pd.read_csv(path)
    df['Country/Region'] = df['Country/Region'].replace('US', 'United States of America')
    
    date_cols = list(df.columns[4:-1])
    country_list = country_list
    cases = [df[df['Country/Region']==country][date_cols] for country in country_list]
    cases = [list(i.T[i.T.columns[0]]) for i in cases]

    fig = go.Figure()
    for i in cases:
        fig.add_trace(go.Scatter(x=date_cols, y=i, name=country_list[cases.index(i)]))
    fig.show()

In [63]:
linear('deaths', ['Brazil', 'United States of America', 'India', 'Argentina'])

In [71]:
world_covid.head()

Province/State Country/Region       Lat       Long  1/22/20  1/23/20  \
0            NaN    Afghanistan  33.93911  67.709953        0        0   
1            NaN        Albania  41.15330  20.168300        0        0   
2            NaN        Algeria  28.03390   1.659600        0        0   
3            NaN        Andorra  42.50630   1.521800        0        0   
4            NaN         Angola -11.20270  17.873900        0        0   

   1/24/20  1/25/20  1/26/20  1/27/20  ...  4/6/21  4/7/21  4/8/21  4/9/21  \
0        0        0        0        0  ...   56779   56873   56943   57019   
1        0        0        0        0  ...  126936  127192  127509  127795   
2        0        0        0        0  ...  117879  118004  118116  118251   
3        0        0        0        0  ...   12328   12363   12409   12456   
4        0        0        0        0  ...   22885   23010   23108   23242   

   4/10/21  4/11/21  4/12/21  4/13/21  4/14/21  iso_a3  
0    57144    57160    57242    57364    57492     AFG  
1   128155   128393   128518   128752   128959     ALB  
2   118378   118516   118645   118799   118975     DZA  
3    12497    12545    12581    12614    12641     NaN  
4    23331    23457    23549    23697    23841     AGO  

[5 rows x 454 columns]

In [88]:
def location(row):
    if row['country'] == 'China':
        if row['province'] == 'Hubei':
            return 'Hubei'
        else:
            return 'Other Chinese Provinces'
    else:
        return 'Rest of the World'

In [80]:
covid19 = pd.read_csv('Data/New/world_covid_clean_2021-04-14.csv')

In [83]:
full_latest = covid19[covid19['date'] == max(covid19['date'])].reset_index()

In [84]:
full_latest

index province      country        lat         lon        date  \
0    120064      NaN  Afghanistan  33.939110   67.709953  2021-04-14   
1    120065      NaN      Albania  41.153300   20.168300  2021-04-14   
2    120066      NaN      Algeria  28.033900    1.659600  2021-04-14   
3    120067      NaN      Andorra  42.506300    1.521800  2021-04-14   
4    120068      NaN       Angola -11.202700   17.873900  2021-04-14   
..      ...      ...          ...        ...         ...         ...   
263  120327      NaN      Vietnam  14.058324  108.277199  2021-04-14   
264  120328      NaN  Cisjordania  31.952200   35.233200  2021-04-14   
265  120329      NaN        Yemen  15.552727   48.516388  2021-04-14   
266  120330      NaN       Zambia -13.133897   27.849332  2021-04-14   
267  120331      NaN     Zimbabwe -19.015438   29.154857  2021-04-14   

     confirmed  deaths  recovered  active  
0        57492    2532      52022    2938  
1       128959    2331      99441   27187  
2       118975    3141      82929   32905  
3        12641     121      11989     531  
4        23841     557      22144    1140  
..         ...     ...        ...     ...  
263       2733      35       2445     253  
264     274690    2923     239291   32476  
265       5582    1083       2128    2371  
266      90389    1229      88241     919  
267      37369    1548      34946     875  

[268 rows x 10 columns]

In [90]:
temp = full_latest.copy()
temp['region'] = temp.apply(location, axis=1)
temp = temp.groupby('region')[['confirmed', 'deaths', 'recovered']].sum().reset_index()
temp = temp.melt(id_vars='region', value_vars=['confirmed', 'deaths', 'recovered'], 
                 var_name='case', value_name='count').sort_values('count')
temp.head()

region       case  count
4  Other Chinese Provinces     deaths    333
3                    Hubei     deaths   4512
7  Other Chinese Provinces  recovered  30572
1  Other Chinese Provinces  confirmed  33963
6                    Hubei  recovered  63640

In [92]:
fig = px.bar(temp, y='region', x='count', color='case', barmode='group', orientation='h',
             height=500, width=1000, text='count', title='Hubei - China - World', 
             color_discrete_sequence= ['#EF553B', '#00CC96', '#636EFA'])
fig.update_traces(textposition='outside')
fig.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
fig.show()

In [ ]:
# Creating a dataframe with total no of confirmed cases for every country
Number_of_countries = len(data['Country/Region'].value_counts())


cases = pd.DataFrame(data.groupby('Country/Region')['Confirmed'].sum())
cases['Country/Region'] = cases.index
cases.index=np.arange(1,Number_of_countries+1)

global_cases = cases[['Country/Region','Confirmed']]
#global_cases.sort_values(by=['Confirmed'],ascending=False)
global_cases

In [ ]:
country_week_latest.isnull().sum()

The ten most affected by Covid-19 pandemic.

In [ ]:
country_week_latest.loc[:, ['country',
                            'confirmed',
                            'deaths']].sort_values(by='confirmed', 
                                                    ascending=False).head(10).style.background_gradient(cmap='Pastel1_r')

In [ ]:
def get_agr_data(df, col1, col2, n):
    df =  df.loc[:, [col1, col2]].sort_values(by=col2, ascending=False).head(n)
    return df.style.background_gradient(cmap='Pastel1_r', text_color_threshold=0)

In [ ]:
get_agr_data(country_week_latest, 'country', 'confirmed', 5)

In [ ]:
get_agr_data(country_week_latest, 'country', 'deaths', 5)

In [ ]:
def get_top_infected_country_by_date(df, col, n):
    '''returns a pandas.io.formats.style.Styler with the last date of Pandemic
    data. Col represent the coluna data to be show, eg. Confirmed.'''
    data = df[df['date'] == max(df['date'])].sort_values(by=col,ascending=False).head(n)
    return data

In [ ]:
get_top_infected_country_by_date(world_covid_grouped, 'confirmed', 2)

In [ ]:
top_10 = get_top_infected_country_by_date(world_covid_grouped, 'deaths', 10)

In [ ]:
top_10['confirmed'].min(), top_10['confirmed'].max()

In [ ]:
ratio = (50000000-0)/(31345985-2286352)

In [ ]:
ratio

In [ ]:
final_value = 0 + ratio*(31345985-0)

In [ ]:
final_value

In [ ]:
plot_hbar(country_wise, 
          'confirmed', 
          'country', 
          15, 
          yesterday, 
          '<b>Top 15 countries with most Covid-19 cases<b>',  
          'Cases', 
          'Country')

In [ ]:
def plot_top_n_hbar(df, xcol, ycol, date, figtitle, xtitle, ytitle, hover_data=[], is_save=False):
    fig = px.bar(df,
                 x=xcol, 
                 y=ycol, 
                 color=ycol,  
                 text=xcol, 
                 orientation='h', 
                 width=900, 
                 hover_data=hover_data,
                 color_discrete_sequence = px.colors.qualitative.Dark24)
    fig.update_layout(title=f'<b>{figtitle}<b> ( {date} )', 
                      xaxis_title=f'<b>{xtitle}<b>', 
                      yaxis_title=f'<b>{ytitle}<b>', 
                      yaxis_categoryorder = 'total ascending',
                      uniformtext_minsize=8, 
                      uniformtext_mode='hide')
    if is_save:
        fig.write_html(f'{figtitle}_{date}.html', auto_open=False)    
    fig.show()

In [ ]:
plot_top_n_hbar(top_10, 
                'deaths', 
                'country', 
                yesterday, 
                'Ten most affected country by Covid-19 fatalities', 
                'Fatalities', 
                'Countries', 
                hover_data=['deaths'], 
                is_save=False)

In [ ]:
# top = top_10['country'].to_list()

In [ ]:
# plt.subplots(figsize=(25,15))
# wordcloud = WordCloud(background_color='white',
#                       width=1920,
#                       height=1080
#                       ).generate(" ".join(top))
# plt.imshow(wordcloud)
# plt.axis('off')
# plt.savefig('Data/New/country.png')
# plt.show()

In [ ]:
# fig = px.choropleth(world_covid_grouped, 
#                     locations="country", 
#                     color=np.log(world_covid_grouped["confirmed"]),
#                     locationmode='country names', 
#                     hover_name="country",
#                     animation_frame=world_covid_grouped["date"].dt.strftime('%Y-%m-%d'),
#                     title='<b>Cases over time<b> (log scale)',
#                     color_continuous_scale='matter')
# fig.update(layout_coloraxis_showscale=True)
# fig.write_html(f'Graficos/World_covid_animation_confirmed_{yesterday}.html', auto_open=False)
# fig.show()

In [ ]:
# def plot_map(df, col_value,col_locations, date, pallet, fig_name, is_save=False):
#     df = df[df[col_value] > 0]
#     fig = px.choropleth(df, 
#                         locations=col_locations, 
#                         locationmode='country names',
#                         color=col_value, 
#                         hover_name=col_locations, 
#                         title=f'<b>Covid country wise {col_value} cases ( {date })<b>', 
#                         hover_data=[col_value], 
#                         color_continuous_scale=pallet,
#                         fitbounds='geojson',
#                         projection='natural earth',
#                        )
#     fig.write_html(f'{fig_name}.html', auto_open=False)
#     fig.show()

In [ ]:
# pal = px.colors.sequential.Viridis
# fig_name = f'Graficos/world_cases_static_{yesterday}'
# plot_map(world_covid_grouped, 'deaths', 'country', yesterday, pal, fig_name, True)

In [ ]:
# def plot_area(df, col_x, col_y, col_color, title, date, path, is_save=False):
#     fig = go.Figure()
#     fig = px.area(df, 
#                   x=col_x, 
#                   y=col_y, 
#                   color=col_color, 
#                   height=600, 
#                   width=700,
#                   title=f'<b>{title} ({date})<b>', 
#                   color_discrete_sequence = [rec, dth, act])
#     if is_save:
#         fig.write_html(f'{path}/{title}_{date}.html', auto_open=False)
#     fig.show()

In [ ]:
# plot_area(word_cases, 
#           'date', 
#           'counts', 
#           'cases', 
#           'World covid-19 cases', 
#           date=yesterday, 
#           path="Graficos",
#           is_save=True)